In [ ]:
## Code for lecture 1: Low-rank solution of Sylvester equation AX + XB = C using ALS
import numpy as np
import matplotlib.pyplot as plt

m = 50
n = 50
k = 15

# Consider case m=n and A = B = L = tridiag(-1,2,-1)*(n+1)^2 is the FD matrix
FD = (np.diag(2*np.ones(n)) + np.diag(-1*np.ones(n-1),1) + np.diag(-1*np.ones(n-1),-1))*(n+1)**2
A = FD
B = FD

# Assume right hand side has rank-one, e.g. constant one function or just random
C = np.ones([m,n])
#C = np.random.randn(m,1)@np.random.randn(1,n)

## First solve matrix equation exactly (naive code works only for "small" matrices)
if max(m,n) <= 50:
    M = np.kron(np.eye(m),A) + np.kron(B,np.eye(n))
    vecC = np.reshape(C,[m*n,1],'F')
    vecXsol = np.linalg.solve(M,vecC)
    Xsol = np.reshape(vecXsol,[m,n],order='F')

    # Visualize solution and its singular values
    print("Relative residual =",np.linalg.norm(M@vecXsol - vecC))
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(5, 2))
    ax1.imshow(Xsol)
    ax2.semilogy(np.linalg.svd(Xsol,compute_uv=False))
    fig.tight_layout()

## Next find low-rank solution X ~ L@R.T using ALS with rank k
als_it = 5
res = np.zeros(als_it)

# initial guess for R
R = np.random.randn(n,k)

# ALS algorithm (with simple solution of substeps)
for t in range(als_it):
    
    # L update
    P, _ = np.linalg.qr(R)
    M_L = np.kron(np.eye(k),A) + np.kron(P.T@B@P,np.eye(m))
    L = np.reshape(np.linalg.solve(M_L,np.reshape(C@P,[m*k,1],'F')),[m,k],'F')
    
    # R update
    Q, _ = np.linalg.qr(L)
    MR = np.kron(np.eye(k),B) + np.kron(Q.T@A@Q,np.eye(n))
    R = np.reshape(np.linalg.solve(MR,np.reshape(C.T@Q,[n*k,1],'F')),[n,k],'F')
    # residual
    res[t]=np.linalg.norm((A@Q)@R.T + Q@(R.T@B) - C)

# Plot ALS residual history and visualize final solution
fig2, (ax3, ax4) = plt.subplots(1, 2, figsize=(5, 2))
ax4.semilogy(res)
ax3.imshow(Q@R.T)
fig2.tight_layout()
plt.show()